# Análisis Dataset de "Inside Airbnb" : ESTAMBUL


<center><img src="https://www.miladoviajero.com/wp-content/uploads/Estambul-mapa.jpg"></center>

# 1. Introducción

"Inside Airbnb" es un sitio web que publica información sobre los alojamientos que se encuentran rentados bajo la plataforma de plataforma Airbnb. 
Este sitio web busca mostrar el impacto que tiene esta plataforma en el mercado de la vivienda para cada ciudad.
Me decidí por seleccionar la ciudad de Estambul por ser una ciudad con mucha historia, cultura y además de su cultura gastronómica.

¿Sabías que es la única ciudad del mundo que se encuentra entre dos continentes, Asia y Europa? 


**Objetivo de análisis**:

El objetivo de este análisis es ver cómo es la oferta de alojamientos en esta ciudad y ver si alguna variable influye en función de la respuesta de los huéspedes.

* ¿La ubicación es importante para el huésped?
* ¿El tipo de habitación es importante para el huésped?
* ¿Un tiempo de respuesta se relaciona con más reservas?
* ¿Al usuario parece importarle que el host tenga la calificación de superhost?



# 2. Librerías

In [7]:
import numpy as np
import pandas as pd


#to make graphs
import matplotlib.pyplot as plt
import seaborn as sns

#to make the plotly graphs
import plotly.graph_objs as go
import plotly.express as px

#to make maps
import geopandas as gpd

# warnings
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)
warnings.filterwarnings("ignore", category=RuntimeWarning)

# 3. Lectura de Datasets

### Lectura de los datasets

In [9]:
listings = pd.read_csv("data/listings.csv", index_col= "id")
listings_details = pd.read_csv("data/listings_details.csv", index_col= "id", low_memory=False)

calendar = pd.read_csv('data/calendar.csv', parse_dates=['date'], index_col=['listing_id']).reset_index()
reviews_details = pd.read_csv("data/reviews_details.csv", parse_dates=['date']).reset_index()
neighbourhoods = pd.read_csv("data/neighbourhoods.csv").reset_index()

# 4. Limpieza de Datos

Fuente: http://insideairbnb.com/get-the-data.html 

En la web podemos encontrarnos con 7 documentos:

* listings.cvs 
* listings_details.cvs
* calendar.csv
* reviews.csv
* reviews_details.csv
* neighbourhoods.csv
* neighbourhoods.geojson

Se utilizaron los datasets: listings.cvs y listings_details.cvs para realizar los análisis y el modelo predictivo. Y el documento neighbourhoods.geojson para realizar los mapas.


### Funciones de análisis

Definimos estas funciones para poder usarla en los 6 datasets y analizar su contenido

In [10]:
def reporte (df):   
    """ Esta función recibe un df y nos imprime un reporte inicial del df"""
    
    print('El df esta formado por: ', df.shape[0], 'filas y', df.shape[1], 'columnas')
    print('Cantidad de valores duplicados: ',df.duplicated().sum())
    print('Cantidad de valores nulos: ', df.isnull().sum().sum())
    # print('Primeras filas del df:')
    # return df.head(3) # Imprimimos las primeras filas para ver las columnas y asi tener una primera vista de lo que hay en el df

In [11]:
def percentage_null (df):
    missing_data = pd.isnull(df).sum()
    missing_data_percentage = missing_data/len(df)*100 #Calculamos el % del los datos faltantes en cada columna
    nulos_totales= missing_data_percentage.sort_values(ascending = False) #Ordenamos de mayor a menor
    nulos_totales = pd.DataFrame(nulos_totales,columns=["% nulos"])
    return nulos_totales.round(2)

## 4.1 Dataset: listings

#### Contenido de las columnas

* ***id***: Airbnb's unique identifier for the listing
* ***name***: Name of the listing
* ***host_id***: Airbnb's unique identifier for the host/user
* ***host_name***: Name of the host. Usually just the first name(s).
* ***neighbourhood_group***: The neighbourhood group as geocoded using the latitude and longitude against neighborhoods as defined by open or public digital shapefiles.
* ***neighbourhood***: The neighbourhood as geocoded using the latitude and longitude against neighborhoods as defined by open or public digital shapefiles.
* ***latitude***: Uses the World Geodetic System (WGS84) projection for latitude and longitude.
* ***longitude***: Uses the World Geodetic System (WGS84) projection for latitude and longitude.
* ***room_type***: All homes are grouped into the following three room types: 1. Entire home/apt 2. Private room 3. Shared room|Hotel]
* ***price***: daily price in local currency. Note, $ sign may be used despite locale
* ***minimum_nights***: minimum number of night stay for the listing (calendar rules may be different)
* ***number_of_reviews***: The number of reviews the listing has
* ***last_review***: The date of the last/newest review
* ***calculated_host_listings_count***: The number of listings the host has in the current scrape, in the city/region geography.
* ***availability_365***: avaliability_x. The availability of the listing x days in the future as determined by the calendar. Note a listing may be available because it has * been booked by a guest or blocked by the host.
* ***number_of_reviews_ltm***: The number of reviews the listing has (in the last 12 months)
* ***license***: The licence/permit/registration number


### Informe inicial

In [12]:
# Usamos esta función para tener en un solo informe que es lo que tenemos en nuestro df
reporte(listings)

El df esta formado por:  41501 filas y 17 columnas
Cantidad de valores duplicados:  8
Cantidad de valores nulos:  118101


## 4.2 Dataset: listings_details

### Informe inicial

In [13]:
reporte(listings_details)

El df esta formado por:  41501 filas y 74 columnas


Cantidad de valores duplicados:  0
Cantidad de valores nulos:  503873


Dado que el este data frame tiene 74 columnas seleccionamos las columnas que necesitamos para nuestro analisis.
Cremaos la variable columnas con un total de 19 variables que hemos seleccionado para nuestro análisis.


In [14]:
columns = ["property_type", "accommodates", "first_review", "review_scores_value", "review_scores_cleanliness", "review_scores_location", "review_scores_accuracy", "review_scores_communication", "review_scores_checkin", "review_scores_rating", "maximum_nights", "listing_url", "host_is_superhost", "host_about", "host_response_time", "host_response_rate", "host_listings_count","number_of_reviews_ltm","reviews_per_month"]

## 4.3 Merge : listings & listings_details

In [15]:
df = pd.merge(listings, listings_details[columns], on='id', how='left')

In [16]:
# Dataset para poner en app antes de limpieza.
#guardamos nuestro df 
df.to_csv('df.csv', header=True, index=False)

In [17]:
reporte(df)

El df esta formado por:  41501 filas y 36 columnas
Cantidad de valores duplicados:  0
Cantidad de valores nulos:  321467


### Eliminación de columnas con valores nulos

In [18]:
# Vemos el % de columnas con valores nulos
percentage_null(df).T

license  neighbourhood_group  host_about  review_scores_checkin  \
% nulos    100.0                100.0       59.65                  42.55   

         review_scores_location  review_scores_value  \
% nulos                   42.55                42.55   

         review_scores_communication  review_scores_accuracy  \
% nulos                        42.55                   42.55   

         review_scores_cleanliness  reviews_per_month_y  ...  longitude  \
% nulos                      42.55                42.26  ...        0.0   

         host_id  room_type  price  minimum_nights  number_of_reviews  \
% nulos      0.0        0.0    0.0             0.0                0.0   

         calculated_host_listings_count  availability_365  \
% nulos                             0.0               0.0   

         number_of_reviews_ltm_x  accommodates  
% nulos                      0.0           0.0  

[1 rows x 36 columns]

Las columnas license y neighbourhood_group presentan un 100% de porcentaje nulos se procede a eliminarlas.


In [19]:
# Como las columnas license y neighbourhood_group presentan un 100% de porcentaje nulos se procede a eliminarlas
df = df.drop(columns=['neighbourhood_group','license'])

In [20]:
# La columna host_about es la descripción que hace el host para presentarse, como es una variable que no vamos a utilizar
# procedemos a quiratla de nuestro df.
df = df.drop(columns=['host_about'])

In [21]:
# En la columna name vamos a reemplazar los nulos por la palabra "no_name"
df['name'] = df['name'].fillna("no_name")

Con respecto a resto de las columnas que contienen null y corresponden a reviews no las vamos a reemplazar ya que es mejor trabajar con la información real.

In [22]:
percentage_null(df).T

review_scores_value  review_scores_location  review_scores_checkin  \
% nulos                42.55                   42.55                  42.55   

         review_scores_cleanliness  review_scores_accuracy  \
% nulos                      42.55                   42.55   

         review_scores_communication  reviews_per_month_y  \
% nulos                        42.55                42.26   

         reviews_per_month_x  last_review  review_scores_rating  ...  \
% nulos                42.26        42.26                 42.26  ...   

         calculated_host_listings_count  number_of_reviews  minimum_nights  \
% nulos                             0.0                0.0             0.0   

         price  room_type  longitude  latitude  neighbourhood  host_name  \
% nulos    0.0        0.0        0.0       0.0            0.0        0.0   

         accommodates  
% nulos           0.0  

[1 rows x 33 columns]

### Tranformación de columnas

In [23]:
pd.set_option('display.max_columns', None)

In [24]:
# Usamos el método info para ver como estan compuestas nuestras columnas
print(df.info())

<class 'pandas.core.frame.DataFrame'>
Index: 41501 entries, 25436 to 857756437907689464
Data columns (total 33 columns):
 #   Column                          Non-Null Count  Dtype  
---  ------                          --------------  -----  
 0   name                            41501 non-null  object 
 1   host_id                         41501 non-null  int64  
 2   host_name                       41501 non-null  object 
 3   neighbourhood                   41501 non-null  object 
 4   latitude                        41501 non-null  float64
 5   longitude                       41501 non-null  float64
 6   room_type                       41501 non-null  object 
 7   price                           41501 non-null  int64  
 8   minimum_nights                  41501 non-null  int64  
 9   number_of_reviews               41501 non-null  int64  
 10  last_review                     23964 non-null  object 
 11  reviews_per_month_x             23964 non-null  float64
 12  calculated_host_list

In [25]:
# Podemos ver que el dtype de las columnas estan correctos por lo que no procedemos a realizar ningun cambio
df['host_response_rate'] = pd.to_numeric(df['host_response_rate'].str.strip('%'))

In [26]:
# Cambiamos el contenido de la columna host_is_superhost a través de un diccionario:
# df['host_is_superhost'] = df['host_is_superhost'].replace({'f': False, 't': True})

Se crea una nueva variable (price_euro) con la columna price convertida a euro ya que esta columna viene en moneda local (Lira turca) y así poder tener una mejor comprensión y percepción. 

El tipo de cambio utilizado es de la web de la unión europea:
https://commission.europa.eu/funding-tenders/procedures-guidelines-tenders/information-contractors-and-beneficiaries/exchange-rate-inforeuro_es
El tipo de cambio a la fecha fecha: 26/06/2023 es 1 TRY = 0.04564 EUR


In [27]:
df['price_euro'] = df['price']*0.04564 
df['price_euro'] = df['price_euro'].round(2).astype('int64')

In [28]:
# Ahora si imprimimos el head del df con el que vamos a continuar:
df.head()

name  host_id  host_name  \
id                                                                            
25436   In the forest Sea view Two minutes to the city.   105823      Yesim   
27271              Lovely apartment in perfect location   117026      Mutlu   
304011            Beyoglu / Central with Beautiful View  1564870     Living   
304029               Zero km to City Center -- Friendly  1564916       Esen   
28277                  Duplex Apartment 11 with Terrace   121607  Alen Ziya   

       neighbourhood  latitude  longitude        room_type  price  \
id                                                                  
25436       Besiktas  41.07883   29.03863  Entire home/apt   2085   
27271        Beyoglu  41.03254   28.98153  Entire home/apt   1044   
304011       Beyoglu  41.03537   28.97316  Entire home/apt   1118   
304029         Sisli  41.05156   28.99052     Private room    384   
28277          Sisli  41.04672   28.98402  Entire home/apt   1857   

        minimum_nights  number_of_reviews last_review  reviews_per_month_x  \
id                                                                           
25436               25                  0         NaN                  NaN   
27271               10                  4  2022-11-01                 0.04   
304011              28                 28  2023-03-18                 0.26   
304029               2                 36  2023-01-05                 0.27   
28277               10                  8  2022-11-26                 0.35   

        calculated_host_listings_count  availability_365  \
id                                                         
25436                                1               348   
27271                                1               266   
304011                               2               240   
304029                               1                94   
28277                               20               361   

        number_of_reviews_ltm_x              property_type  accommodates  \
id                                                                         
25436                         0         Entire rental unit             3   
27271                         1         Entire rental unit             2   
304011                        7         Entire rental unit             4   
304029                        1       Private room in loft             2   
28277                         6  Entire serviced apartment             5   

       first_review  review_scores_value  review_scores_cleanliness  \
id                                                                    
25436           NaN                  NaN                        NaN   
27271    2014-10-20                 5.00                       4.75   
304011   2014-05-12                 4.63                       4.93   
304029   2012-05-07                 4.91                       4.94   
28277    2021-05-15                 4.75                       4.75   

        review_scores_location  review_scores_accuracy  \
id                                                       
25436                      NaN                     NaN   
27271                     5.00                    5.00   
304011                    4.59                    4.85   
304029                    4.79                    4.88   
28277                     5.00                    5.00   

        review_scores_communication  review_scores_checkin  \
id                                                           
25436                           NaN                    NaN   
27271                          5.00                   5.00   
304011                         4.93                   4.96   
304029                         5.00                   5.00   
28277                          5.00                   4.88   

        review_scores_rating  maximum_nights  \
id                                             
25436                    NaN            1125   
27271                   5.00

## 4.4 Dataset: calendar

Este Dataframe muestra la disponibiiad que tiene el alojamiento desde el 2023-03-31  al  2024-04-02.
No lo vamos a ultilizar para nuestro análisis por lo cual no vamos a avanzar con su análisis

### Informe inicial

In [29]:
reporte(calendar)

El df esta formado por:  15146021 filas y 7 columnas


Cantidad de valores duplicados:  0
Cantidad de valores nulos:  68


In [30]:
calendar.head(3)

listing_id       date available      price adjusted_price  minimum_nights  \
0       25436 2023-03-31         f  $2,085.00      $2,085.00            25.0   
1       25436 2023-04-01         f  $2,085.00      $2,085.00            25.0   
2       25436 2023-04-02         f  $2,085.00      $2,085.00            25.0   

   maximum_nights  
0          1125.0  
1          1125.0  
2          1125.0

In [31]:
print('Período de fechas de análisis', calendar['date'].min(), ' - ', calendar['date'].max())

Período de fechas de análisis 2023-03-31 00:00:00  -  2024-04-02 00:00:00


## 4.4 Dataset: reviews_details

Este dataset contiene las reviwes de que han tenido los alojamientos, como esta información la podemos obtener en los datasets de listings en esta oportunidad no se usarán para el análisis.

Período de análisis 2010-06-14 - 2023-04-01

### Informe inicial

In [32]:
reporte(reviews_details)

El df esta formado por:  416940 filas y 7 columnas


Cantidad de valores duplicados:  0
Cantidad de valores nulos:  21


In [33]:
reviews_details.head()

index  listing_id                  id       date  reviewer_id  \
0      0       27271            21619434 2014-10-20     17033378   
1      1      304029             1242627 2012-05-07      2224284   
2      2       27271           260206599 2018-05-04     34086382   
3      3       27271  535927099037466665 2022-01-09    419733560   
4      4       27271  750456812858706901 2022-11-01    132525657   

     reviewer_name                                           comments  
0         Hortense  En l'absence de Mutlu, sa voisine adorable nou...  
1  Tim And Nandini  Stayed with my girlfriend at Esen's apartment....  
2            Marie  Appartement très agréable, bien situé.<br/>Mut...  
3           Daniel                                                5/5  
4             Paul  The apartment certainly looks better than in p...

In [34]:
print('Período de análisis', reviews_details['date'].min(), ' - ', reviews_details['date'].max())

Período de análisis 2010-06-14 00:00:00  -  2023-04-01 00:00:00


## 4.5 Dataset: neighbourhoods

Este dataframe contiene una lista de todos los vecindarios que presenta nuetro df.

Como esta información también la podemos obtener en los datasets de listings en esta oportunidad no se usarán para el análisis.


### Informe inicial

In [35]:
reporte(neighbourhoods)

El df esta formado por:  39 filas y 3 columnas
Cantidad de valores duplicados:  0
Cantidad de valores nulos:  39


In [36]:
# Cantidad de vecindarios:
neighbourhoods['neighbourhood'].sort_values().count()

39

In [37]:
neighbourhoods.head()

index  neighbourhood_group neighbourhood
0      0                  NaN        Adalar
1      1                  NaN    Arnavutkoy
2      2                  NaN      Atasehir
3      3                  NaN       Avcilar
4      4                  NaN      Bagcilar

# 5. Análisis Exporatorio de Datos

Ahora tenemos un df listo para realizar el análisis exploratorio. TEniedo en cuenta que los nulos corresponden a las columnas de reviews


In [38]:
reporte(df)

El df esta formado por:  41501 filas y 34 columnas
Cantidad de valores duplicados:  0
Cantidad de valores nulos:  213686


### ¿Cómo se distribuyen los alojamientos en Estambul en general?

Distritos: Estambul esta dividida por 39 distritos en los cuales podemos ver según la gráfica y en el mapa que la mayoría de los hospedajes se encuentran en los distritos de: Beyoglu, Sisli, Kadikoy y Fatih.
* Beyoglu: es la zona donde las comunidades extranjeras establecieron las embajadas y las iglesias, y donde en el siglo XX se levantaron grandes hoteles y tiendas más lujosas.
* Sisli: es el distrito de cines y lugares de ocio. Aquí se encuentran entre otras cosas salas de conciertos y teatros.
* Kadikoy: es un distrito residencial y es conocido por su mercado de pescado y productos agrícolas y por lo general los turistas y locales aprovecha a comprar especias, tés o frutos secos.
* Fatih: es el distrito donde se encuentra su barrio histórico, aquí se encuentra La mezquita de Fatih, que es una de las mas grandes de la ciudad, así como también el acueducto romano ente otras tantos edificios y monumentos históricos.


In [39]:
colors = ['#AF1D56', '#FFDE59', '#CB6CE6', '#FF914D']

In [61]:
# Cantidad de Barios

neighbourhood=df['neighbourhood'].value_counts().sort_values(ascending=True)
fig1 = px.bar(neighbourhood, orientation='h', 
       template= "plotly_dark",
       color_discrete_sequence = [colors[3]],
       height=800    
       )
fig1.update_layout(
       title='Distribución de distritos',
       xaxis=dict(title='cantidades'),
       yaxis=dict(title=''),
       showlegend=False
    )


In [64]:
# Cantidad de Alojamientos por Distritos

dfneighbourhood = pd.DataFrame(neighbourhood)
dfneighbourhood = dfneighbourhood.reset_index()
adam = gpd.read_file("data/neighbourhoods.geojson")
fig3 = px.choropleth_mapbox(dfneighbourhood, geojson=adam, featureidkey='properties.neighbourhood',locations ="neighbourhood",color = 'count', 
                            color_continuous_scale='magma', title="Distritos de Estambul",zoom=10, hover_data = ['neighbourhood','count'],
                            mapbox_style="carto-positron",width=1000, height=750,center = {"lat": 41.0037, "lon": 28.9737})
fig3.update(layout_coloraxis_showscale=True)
fig3.update_layout( paper_bgcolor="#fff",font_color="#AF1D56",title_font_size=40, title_x = 0.5)
fig3.update_layout(legend=dict(title=""))
fig3.show()

### ¿Cómo varía el precio de los alojamientos?

In [67]:
price_mean = df.groupby('neighbourhood')['price_euro'].mean().round(2).sort_values(ascending=True)
dfprecio = pd.DataFrame(price_mean)
dfprecio = dfprecio.reset_index()
#ahora graficamos con plotly
fig3 = px.area(dfprecio, x="neighbourhood", y="price_euro",
        template= "plotly_dark", 
        title = "Average daily price based on location in Amsterdam",
        color_discrete_sequence = [colors[2]] 
        )

fig3.update_layout(
       title='Precio promedio de alojamientos por distrito',
       xaxis=dict(title='distritos'),
       yaxis=dict(title='euros'),
       showlegend=False
    )

In [43]:
df['price'].mean()

2007.3427869207972

In [44]:
df['price_euro'].mean()

91.12146695260356

In [45]:
dfprice_meand = pd.DataFrame(price_mean)
dfneighbourhood = dfprice_meand.reset_index()
adam = gpd.read_file("data/neighbourhoods.geojson")
fig3 = px.choropleth_mapbox(dfneighbourhood, geojson=adam, featureidkey='properties.neighbourhood',locations ="neighbourhood",color = 'price_euro', 
                            color_continuous_scale='magma', title="Average Price Per District",zoom=10, hover_data = ['neighbourhood','price_euro'],
                            mapbox_style="carto-positron",width=1000, height=750,center = {"lat": 41.0037, "lon": 28.9737})
fig3.update(layout_coloraxis_showscale=True)
fig3.update_layout( paper_bgcolor="#fff",font_color="#AF1D56",title_font_size=40, title_x = 0.5)
fig3.show()

### ¿Qué tipos de alojamientos se ofrecen?


Con este gráfico podemos ver los diferentes tipos de alojamientos ofrecido.
Por un lado, están los tipos de habitación: 
* Entire home/apt - (**Casa/apartamento completo**)
* Private room - (**Habitación privada**)
* Hotel room - (**Habitación de hotel**)
* Shared room - (**Habitación compartida**)

 Luego están los diferentes tipos de alojamientos: en los que se pueden diferenciar 109 diferentes tipos. 
 Por lo que podemos tener:“Entire serviced apartment”, que corresponden a apartamento completo con servicio hasta “Private room in tent” que son Habitación privada en tienda de campaña.

Lo que se puede ver que lo que mas se predomina es Casa/apartamento completo con mas de la mitad de los datos.
 



In [71]:
rooms = df.groupby(['neighbourhood', 'room_type','property_type','accommodates']).size().reset_index(name='Count')

# Crear el gráfico de barras agrupadas
fig = px.treemap(rooms, path=['room_type','property_type'], values='Count', 
                 color_discrete_sequence=colors, template='plotly_dark')

fig.update_layout(
    title='Distribución por tipo de habitación y tipo de propiedad',
    xaxis=dict(title='Edad'),
    yaxis=dict(title='Cantidad'),
    bargap=0.1,
    showlegend=True
)
fig.show()


In [48]:
df['room_type'].unique()

array(['Entire home/apt', 'Private room', 'Hotel room', 'Shared room'],
      dtype=object)

In [49]:
# df['property_type'].unique()

In [68]:
fig5 = px.histogram(df,'room_type',
             nbins = 20,
             template= "plotly_dark",
             color_discrete_sequence = [colors[1]])

fig5.update_layout(
       title='Tipos de habitación',
    #    xaxis=dict(title='room_type'),
    #    yaxis=dict(title='Count'),
       showlegend=False
)
fig5.show()

In [70]:
# Cantidad de Barios

propertytype=df['property_type'].value_counts().sort_values(ascending=False).head(10)
fig1 = px.bar(propertytype, 
       template= "plotly_dark",
       color_discrete_sequence = [colors[3]],
    #    height=800    
       )
fig1.update_layout(
       title='Tipos de habitación (Top 10)',
       # xaxis=dict(title='Property_type'),
       # yaxis=dict(title='Count'),
       # showlegend=False
)

### ¿Cómo son los propietarios?

In [53]:
df['host_is_superhost'] = df['host_is_superhost'].replace({"t": "Superhost", "f": "No_superhost"})
feq=df['host_is_superhost'].value_counts()

px.pie(feq ,names = feq.index, values=feq.values,width = 1000, 
       template= "plotly_dark",
       color_discrete_sequence = colors,
       title="Number of listings with Superhost")

In [54]:
sh_reviews1 = df[['host_is_superhost','review_scores_value']].value_counts().reset_index().head(15)

In [55]:
sh_reviews1

host_is_superhost  review_scores_value  count
0       No_superhost                 5.00   6522
1          Superhost                 5.00   1613
2       No_superhost                 4.00   1119
3       No_superhost                 4.50    900
4       No_superhost                 4.67    610
5       No_superhost                 3.00    448
6       No_superhost                 4.75    424
7       No_superhost                 1.00    416
8       No_superhost                 4.80    331
9       No_superhost                 4.33    313
10      No_superhost                 4.60    244
11         Superhost                 4.67    223
12         Superhost                 4.75    222
13      No_superhost                 4.71    220
14      No_superhost                 4.83    219

In [60]:
fig7 = px.box(df, x="review_scores_value",y= 'host_is_superhost',
              template="plotly_dark",
              color_discrete_sequence = colors
              )

fig7.update_layout(
    title='Numero de Reseñas',
    xaxis=dict(title='Calificaciones'),
    yaxis=dict(title=''),
    bargap=0.1,
    showlegend=True 
    )
fig7.show()

# 7. conclusiones

CONCLUSIÓN
Después de realizar el análisis del dataset, podemos llegar a las siguientes conclusiones sobre la oferta de alojamientos en la ciudad de Estambul:

* En total, hay 41,500 alojamientos disponibles en la plataforma Airbnb en Estambul.
* Los distritos con la mayor cantidad de ofertas de alojamiento son: Beyoglu, Sisli, Kadikoy y Fatih. Estos distritos destacan por tener una amplia variedad de opciones para los viajeros.
* El precio medio por noche de alojamiento en Estambul es de €91.12. Este valor representa el promedio de los precios de todos los alojamientos disponibles en la ciudad.
* El tipo de alojamiento más comúnmente ofrecido en Estambul es el ***"Casa/apartamento completo"***. Esto significa que la mayoría de los alojamientos disponibles en la plataforma son viviendas completas que los viajeros pueden reservar y disfrutar en su totalidad.
Estas conclusiones nos brindan una idea general sobre la oferta de alojamientos en Estambul a través de Airbnb y nos ayudan a comprender mejor el mercado de alojamiento en la ciudad.


Guardado de DT final

In [58]:
# Dataset para app
#guardamos nuestro df 
# df.to_csv('df_limpio.csv', header=True, index=False) 

In [59]:
# Dataset para powerBi
# #guardamos nuestro df 
# df.to_csv('df_powerbi.csv', header=True, index=False) 